In [10]:
import os
from sklearn.metrics.pairwise import cosine_similarity
import re

file_path = "/Users/sakshmenon/Desktop/results/workflow files/"
os.chdir(file_path)

ref_file = file_path + "s_cerevisiae_protein.csv"
query_file = file_path + "p_carinii_protein.csv"
top_match_file = file_path + "p_carinii2s_cerevisiae.bfs.k3.txt"

In [11]:
def extract_queries(file):
    pattern = r"Query:\s+>([\w.]+)\s.*?\nTop1:\s+[\d.]+\s+>([\w.]+)\s.*?\nTop2:\s+[\d.]+\s+>([\w.]+)\s.*?\nTop3:\s+[\d.]+\s+>([\w.]+)\s"
    
    with open(file) as obj:
        queries = {}
        file_content = obj.read()
        query_top1_pairs = re.findall(pattern, file_content)
        query_top_dict = v = {i[0]: i[1:] for i in query_top1_pairs}
        for id in query_top_dict:
            if id not in queries:
                queries.update({id: query_top_dict[id]})
            else:
                queries[id].append(query_top_dict[id])

        query_IDs = list(queries.keys())
        t_pattern = r"Time:\s+([\d.]+)"
        times = re.findall(t_pattern, file_content)

        pairs = zip(query_IDs, times)
        q_times = {}
        for pair in pairs:
            q_times[pair[0]] = pair[1]

    return queries, q_times


In [12]:
import pandas as pd

def query_ref_df_gen(query_file, ref_file):
    query_df = pd.read_csv(query_file)
    qindex_df = query_df['ProteinID']

    pattern = r">([\w.]+)"
    for index in qindex_df.index:
        query_id = re.findall(pattern, query_df['ProteinID'][index])
        qindex_df[index] = query_id[0]
    
    ref_df = pd.read_csv(ref_file)
    rindex_df = ref_df['ProteinID']

    pattern = r">([\w.]+)"
    for index in rindex_df.index:
        ref_id = re.findall(pattern, ref_df['ProteinID'][index])
        rindex_df[index] = ref_id[0]

    return query_df, qindex_df, ref_df, rindex_df

In [13]:
def score_gen(qindex_df, rindex_df, query_df, ref_df, queries, pairs):
    score_report = []

    for query in qindex_df:
        qindex = qindex_df[qindex_df == query].index[0]
        query_vector = query_df.loc[qindex].values[:-1]
        matches = []
        for inst in queries[query]:
            rindex = rindex_df[rindex_df == inst].index[0]
            ref_vector = ref_df.loc[rindex].values[:-1]
            score = cosine_similarity([query_vector], [ref_vector])
            matches.append(({"ID": inst, "Score": round(float(score[0]), ndigits=5)}))

        sub_report = {'Query': ({"ID": query, "Time" : float(pairs[query]), 'Matches': matches})}
        score_report.append(sub_report)
    
    return score_report

In [14]:
queries, pairs = extract_queries(top_match_file)
query_df, qindex_df, ref_df, rindex_df = query_ref_df_gen(query_file, ref_file)

/var/folders/h3/pl4_4z116_dcntldrzwpn49w0000gn/T/ipykernel_80292/3738089485.py:10: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  qindex_df[index] = query_id[0]
/var/folders/h3/pl4_4z116_dcntldrzwpn49w0000gn/T/ipykernel_80292/3738089485.py:10: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  qindex_df[index] = query_id[0]
/var/folders/h3/pl4_4z116_dcntldrzwpn49w0000gn/T/ipykernel_80292/3738089485.py:10: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus

In [17]:
queries

{'XP_018224486.1': ('NP_013207.1', 'NP_013712.1', 'NP_009961.2'),
 'XP_018225276.1': ('NP_012980.1', 'NP_012719.2', 'NP_012600.1'),
 'XP_018226782.1': ('NP_011967.1', 'NP_012600.1', 'NP_012719.2'),
 'XP_018225744.1': ('NP_010745.3', 'NP_012915.3', 'NP_011700.1'),
 'XP_018224326.1': ('NP_013060.1', 'NP_014157.1', 'NP_015442.1'),
 'XP_018226348.1': ('NP_009465.2', 'NP_009694.3', 'NP_011967.1'),
 'XP_018226646.1': ('NP_013559.1', 'NP_015442.1', 'NP_013188.1'),
 'XP_018225829.1': ('NP_011320.3', 'NP_011833.1', 'NP_012328.1'),
 'XP_018226360.1': ('NP_009551.2', 'NP_011833.1', 'NP_015313.1'),
 'XP_018224465.1': ('NP_009961.2', 'NP_009411.2', 'NP_013526.1'),
 'XP_018225238.1': ('NP_009694.3', 'NP_013408.1', 'NP_012600.1'),
 'XP_018227701.1': ('NP_012035.1', 'NP_116659.1', 'NP_013446.1'),
 'XP_018227408.1': ('NP_012719.2', 'NP_012600.1', 'NP_013490.3'),
 'XP_018227007.1': ('NP_011888.1', 'NP_013187.1', 'NP_012461.1'),
 'XP_018225341.1': ('NP_013934.1', 'NP_014413.1', 'NP_013932.1'),
 'XP_01822

In [29]:
score_report = score_gen(qindex_df, rindex_df, query_df, ref_df, queries, pairs)
score_report

[{'Query': {'ID': 'XP_018224486.1',
   'Time': 0.01055,
   'Matches': [{'ID': 'NP_013207.1', 'Score': 0.90466},
    {'ID': 'NP_013712.1', 'Score': 0.66011},
    {'ID': 'NP_009961.2', 'Score': 0.67377}]}},
 {'Query': {'ID': 'XP_018225276.1',
   'Time': 0.01052,
   'Matches': [{'ID': 'NP_012980.1', 'Score': 0.8769},
    {'ID': 'NP_012719.2', 'Score': 0.74398},
    {'ID': 'NP_012600.1', 'Score': 0.74176}]}},
 {'Query': {'ID': 'XP_018226782.1',
   'Time': 0.01001,
   'Matches': [{'ID': 'NP_011967.1', 'Score': 0.9621},
    {'ID': 'NP_012600.1', 'Score': 0.74338},
    {'ID': 'NP_012719.2', 'Score': 0.73828}]}},
 {'Query': {'ID': 'XP_018225744.1',
   'Time': 0.00979,
   'Matches': [{'ID': 'NP_010745.3', 'Score': 0.95927},
    {'ID': 'NP_012915.3', 'Score': 0.80275},
    {'ID': 'NP_011700.1', 'Score': 0.75829}]}},
 {'Query': {'ID': 'XP_018224326.1',
   'Time': 0.00972,
   'Matches': [{'ID': 'NP_013060.1', 'Score': 0.92685},
    {'ID': 'NP_014157.1', 'Score': 0.7472},
    {'ID': 'NP_015442.1', 

In [30]:
import json

os.chdir('/Users/sakshmenon/Desktop/PLM/Workflow Gen/Report Gen')

json_object = json.dumps(score_report, indent=4)

with open("sample.json", "w") as outfile:
	outfile.write(json_object)


In [8]:
pat = r">([\w.]+)\s.*?"
re.findall(pat, ">CC_013207.1 AAA family ATPase midasin [Saccharomyces cerevisiae S288C]")

['CC_013207.1']

In [18]:
method_name = 'a'
avg_time = 0.4387293
f"Average search time for {method_name}: {avg_time:.5f} seconds"

'Average search time for a: 0.43873 seconds'

In [20]:
os.chdir('/Users/sakshmenon/Desktop/PLM/Workflow Gen/Report Gen')
output_file_obj = open('test', 'w')
output_file_obj.write(f"Average search time for {method_name}: {avg_time:.5f} seconds")
output_file_obj.close()